DENSE RETRIEVAL

In [ ]:
!pip install -U beir

     |████████████████████████████████| 49 kB 2.3 MB/s 
     |████████████████████████████████| 78 kB 4.0 MB/s 
     |████████████████████████████████| 378 kB 49.0 MB/s 
     |████████████████████████████████| 8.4 MB 59.9 MB/s 
     |████████████████████████████████| 4.4 MB 27.4 MB/s 
     |████████████████████████████████| 2.9 MB 21.3 MB/s 
     |████████████████████████████████| 3.3 MB 54.1 MB/s 
     |████████████████████████████████| 1.2 MB 58.5 MB/s 
     |████████████████████████████████| 56 kB 5.6 MB/s 
     |████████████████████████████████| 596 kB 56.8 MB/s 
     |████████████████████████████████| 895 kB 62.3 MB/s 
  Created wheel for pytrec-eval: filename=pytrec_eval-0.5-cp37-cp37m-linux_x86_64.whl size=265065 sha256=b8b8c5e739200c87a6d4d475fd0382ef0157cc9c99aad76f4d35e33dc2cdb3f2
  Stored in directory: /root/.cache/pip/wheels/42/96/77/0829b8b2606f90f61ba10a51277629d2b615604e122ee932f4
  Created wheel for sentence-transformers: filename=sentence_transformers-2.1.0-py3-none-an

In [ ]:
import pathlib, os
import time
import pandas as pd
import random
import requests
import json
import torch
import torch.multiprocessing as mp
from tqdm.notebook import tqdm
from tqdm.autonotebook import trange
from beir import util, LoggingHandler
from beir.retrieval.evaluation import EvaluateRetrieval
from beir.retrieval import models
from beir.retrieval.search.dense import DenseRetrievalExactSearch as DRES
from beir.datasets.data_loader import GenericDataLoader

In [ ]:
def load(dataset):
  hostname = 'localhost'
  index_name = dataset
  url = 'https://public.ukp.informatik.tu-darmstadt.de/thakur/BEIR/datasets/{}.zip'.format(dataset)
  out_dir = os.path.join(os.getcwd(), 'datasets')
  data_path = util.download_and_unzip(url, out_dir)
  return GenericDataLoader(data_path).load(split='test') # 'test', 'train', 'dev'


In [ ]:
def retrieve(corpus, queries, qrels, model_name, batch_size, score_function):
  if batch_size is None:
    dr_model = EvaluateRetrieval(DRES(models.SentenceBERT(model_name)), score_function=score_function)
  else:
    dr_model = EvaluateRetrieval(
        DRES(models.SentenceBERT(model_name), batch_size=batch_size), score_function=score_function)
  res_model = dr_model.retrieve(corpus, queries)
  return dr_model.evaluate(qrels, res_model, dr_model.k_values)

In [ ]:
def evaluate(corpus, queries, qrels, model_name, batch_size, score_function):
  ndcg, _map, recall, precision = retrieve(corpus, queries, qrels, model_name, batch_size, score_function)
  c_map = 'MAP@10'
  c_map_h = 'MAP@100'
  c_map_t = 'MAP@1000'
  c_ndcg = 'NDCG@10'
  c_ndcg_h = 'NDCG@100'
  c_ndcg_t = 'NDCG@1000'
  c_pre = 'P@10'
  c_pre_h = 'P@100'
  c_pre_t = 'P@1000'
  c_rec = 'Recall@10'
  c_rec_h = 'Recall@100'
  c_rec_t = 'Recall@1000'
  eval_dict = {
      c_map: [_map[c_map]], 
      c_map_h: [_map[c_map_h]],
      c_map_t: [_map[c_map_t]],
      c_ndcg: [ndcg[c_ndcg]], 
      c_ndcg_h: [ndcg[c_ndcg_h]],
      c_ndcg_t: [ndcg[c_ndcg_t]],
      c_pre: [precision[c_pre]], 
      c_pre_h: [precision[c_pre_h]],
      c_pre_t: [precision[c_pre_t]],
      c_rec: [recall[c_rec]],
      c_rec_h: [recall[c_rec_h]],
      c_rec_t: [recall[c_rec_t]]}
  eval_df = pd.DataFrame(data=eval_dict)
  eval_df.index = [model_name]
  return eval_df

In [ ]:
tc_corpus, tc_queries, tc_qrels = load('webis-touche2020')
tc_als = evaluate(tc_corpus, tc_queries, tc_qrels, 'allenai-specter', 128, 'dot')
tc_amp = evaluate(tc_corpus, tc_queries, tc_qrels, 'all-mpnet-base-v2', 128, 'dot')
tc_adr = evaluate(tc_corpus, tc_queries, tc_qrels, 'all-distilroberta-v1', 128, 'dot')
tc_aml = evaluate(tc_corpus, tc_queries, tc_qrels, 'all-MiniLM-L12-v2', 128, 'dot')
tc_mmp = evaluate(tc_corpus, tc_queries, tc_qrels, 'multi-qa-mpnet-base-dot-v1', 128, 'dot')
tc_mml = evaluate(tc_corpus, tc_queries, tc_qrels, 'multi-qa-MiniLM-L6-cos-v1', 128, 'cos_sim')
tc_mdd = evaluate(tc_corpus, tc_queries, tc_qrels, 'multi-qa-distilbert-dot-v1', 128, 'dot')
tc_mdc = evaluate(tc_corpus, tc_queries, tc_qrels, 'multi-qa-distilbert-cos-v1', 128, 'cos_sim')
tc_msdd = evaluate(tc_corpus, tc_queries, tc_qrels, 'msmarco-distilbert-base-tas-b', 128, 'dot')
tc_msdc = evaluate(tc_corpus, tc_queries, tc_qrels, 'msmarco-distilbert-dot-v5', 128, 'dot')
tc_msbc = evaluate(tc_corpus, tc_queries, tc_qrels, 'msmarco-bert-co-condensor', 128, 'dot')
tc_msra = evaluate(tc_corpus, tc_queries, tc_qrels, 'msmarco-roberta-base-ance-firstp', None, 'dot')

/content/datasets/webis-touche2020.zip:   0%|          | 0.00/217M [00:00<?, ?iB/s]

  0%|          | 0/382545 [00:00<?, ?it/s]

Downloading:   0%|          | 0.00/690 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.71k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/622 [00:00<?, ?B/s]

...

Batches:   0%|          | 0/391 [00:00<?, ?it/s]

Batches:   0%|          | 0/391 [00:00<?, ?it/s]

Batches:   0%|          | 0/391 [00:00<?, ?it/s]

Batches:   0%|          | 0/391 [00:00<?, ?it/s]

Batches:   0%|          | 0/255 [00:00<?, ?it/s]

In [ ]:
ag_corpus, ag_queries, ag_qrels = load('arguana')
ag_als = evaluate(ag_corpus, ag_queries, ag_qrels, 'allenai-specter', 128, 'dot')
ag_amp = evaluate(ag_corpus, ag_queries, ag_qrels, 'all-mpnet-base-v2', 128, 'dot')
ag_adr = evaluate(ag_corpus, ag_queries, ag_qrels, 'all-distilroberta-v1', 128, 'dot')
ag_aml = evaluate(ag_corpus, ag_queries, ag_qrels, 'all-MiniLM-L12-v2', 128, 'dot')
ag_mmp = evaluate(ag_corpus, ag_queries, ag_qrels, 'multi-qa-mpnet-base-dot-v1', 128, 'dot')
ag_mml = evaluate(ag_corpus, ag_queries, ag_qrels, 'multi-qa-MiniLM-L6-cos-v1', 128, 'cos_sim')
ag_mdd = evaluate(ag_corpus, ag_queries, ag_qrels, 'multi-qa-distilbert-dot-v1', 128, 'dot')
ag_mdc = evaluate(ag_corpus, ag_queries, ag_qrels, 'multi-qa-distilbert-cos-v1', 128, 'cos_sim')
ag_msdd = evaluate(ag_corpus, ag_queries, ag_qrels, 'msmarco-distilbert-base-tas-b', 128, 'dot')
ag_msdc = evaluate(ag_corpus, ag_queries, ag_qrels, 'msmarco-distilbert-dot-v5', 128, 'dot')
ag_msbc = evaluate(ag_corpus, ag_queries, ag_qrels, 'msmarco-bert-co-condensor', 128, 'dot')
ag_msra = evaluate(ag_corpus, ag_queries, ag_qrels, 'msmarco-roberta-base-ance-firstp', None, 'dot')

/content/datasets/arguana.zip:   0%|          | 0.00/3.60M [00:00<?, ?iB/s]

  0%|          | 0/8674 [00:00<?, ?it/s]

Batches:   0%|          | 0/11 [00:00<?, ?it/s]

Batches:   0%|          | 0/68 [00:00<?, ?it/s]

Batches:   0%|          | 0/11 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/68 [00:00<?, ?it/s]

Batches:   0%|          | 0/11 [00:00<?, ?it/s]

Batches:   0%|          | 0/68 [00:00<?, ?it/s]

Batches:   0%|          | 0/11 [00:00<?, ?it/s]

Batches:   0%|          | 0/68 [00:00<?, ?it/s]

In [ ]:
fq_corpus, fq_queries, fq_qrels = load('fiqa')
fq_als = evaluate(fq_corpus, fq_queries, fq_qrels, 'allenai-specter', 128, 'dot')
fq_amp = evaluate(fq_corpus, fq_queries, fq_qrels, 'all-mpnet-base-v2', 128, 'dot')
fq_adr = evaluate(fq_corpus, fq_queries, fq_qrels, 'all-distilroberta-v1', 128, 'dot')
fq_aml = evaluate(fq_corpus, fq_queries, fq_qrels, 'all-MiniLM-L12-v2', 128, 'dot')
fq_mmp = evaluate(fq_corpus, fq_queries, fq_qrels, 'multi-qa-mpnet-base-dot-v1', 128, 'dot')
fq_mml = evaluate(fq_corpus, fq_queries, fq_qrels, 'multi-qa-MiniLM-L6-cos-v1', 128, 'cos_sim')
fq_mdd = evaluate(fq_corpus, fq_queries, fq_qrels, 'multi-qa-distilbert-dot-v1', 128, 'dot')
fq_mdc = evaluate(fq_corpus, fq_queries, fq_qrels, 'multi-qa-distilbert-cos-v1', 128, 'cos_sim')
fq_msdd = evaluate(fq_corpus, fq_queries, fq_qrels, 'msmarco-distilbert-base-tas-b', 128, 'dot')
fq_msdc = evaluate(fq_corpus, fq_queries, fq_qrels, 'msmarco-distilbert-dot-v5', 128, 'dot')
fq_msbc = evaluate(fq_corpus, fq_queries, fq_qrels, 'msmarco-bert-co-condensor', 128, 'dot')
fq_msra = evaluate(fq_corpus, fq_queries, fq_qrels, 'msmarco-roberta-base-ance-firstp', None, 'dot')

/content/datasets/fiqa.zip:   0%|          | 0.00/17.1M [00:00<?, ?iB/s]

  0%|          | 0/57638 [00:00<?, ?it/s]

Batches:   0%|          | 0/6 [00:00<?, ?it/s]

Batches:   0%|          | 0/391 [00:00<?, ?it/s]

Batches:   0%|          | 0/60 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/391 [00:00<?, ?it/s]

Batches:   0%|          | 0/60 [00:00<?, ?it/s]

Batches:   0%|          | 0/6 [00:00<?, ?it/s]

Batches:   0%|          | 0/391 [00:00<?, ?it/s]

Batches:   0%|          | 0/60 [00:00<?, ?it/s]



---



**TOUCHÉ** - [Homepage](https://webis.de/events/touche-20/) - [Paper](https://www.researchgate.net/publication/344371868_Overview_of_Touche_2020_Argument_Retrieval)

In [ ]:
pd.concat([tc_als, tc_amp, tc_adr, tc_aml, tc_mmp, tc_mml, tc_mdd, tc_mdc, tc_msdd, tc_msdc, tc_msbc, tc_msra])

MAP@10  MAP@100  ...  Recall@100  Recall@1000
allenai-specter                   0.03532  0.06169  ...     0.27132      0.64884
all-mpnet-base-v2                 0.07557  0.12238  ...     0.40980      0.79409
all-distilroberta-v1              0.08344  0.13906  ...     0.45072      0.80799
all-MiniLM-L12-v2                 0.06632  0.11485  ...     0.41017      0.78632
multi-qa-mpnet-base-dot-v1        0.07881  0.12627  ...     0.42313      0.80003
multi-qa-MiniLM-L6-cos-v1         0.06488  0.11654  ...     0.41106      0.80569
multi-qa-distilbert-dot-v1        0.09754  0.14994  ...     0.44583      0.79788
multi-qa-distilbert-cos-v1        0.08505  0.13406  ...     0.42850      0.80636
msmarco-distilbert-base-tas-b     0.06875  0.12285  ...     0.43100      0.81051
msmarco-distilbert-dot-v5         0.08696  0.14169  ...     0.42629      0.79315
msmarco-bert-co-condensor         0.07395  0.12491  ...     0.42412      0.74080
msmarco-roberta-base-ance-firstp  0.09733  0.15387  ...     0.45836      0.79467

[12 rows x 12 columns]



---



**ARGUANA** - [Homepage](http://argumentation.bplaced.net/arguana/data) - [Paper](https://aclanthology.org/P18-1023.pdf)

In [ ]:
pd.concat([ag_als, ag_amp, ag_adr, ag_aml, ag_mmp, ag_mml, ag_mdd, ag_mdc, ag_msdd, ag_msdc, ag_msbc, ag_msra])

MAP@10  MAP@100  ...  Recall@100  Recall@1000
allenai-specter                   0.25379  0.26748  ...     0.85135      0.97013
all-mpnet-base-v2                 0.37692  0.38986  ...     0.98649      0.99644
all-distilroberta-v1              0.38394  0.39514  ...     0.98578      0.99644
all-MiniLM-L12-v2                 0.38083  0.39264  ...     0.97866      0.99573
multi-qa-mpnet-base-dot-v1        0.41450  0.42569  ...     0.98862      0.99644
multi-qa-MiniLM-L6-cos-v1         0.40196  0.41336  ...     0.98222      0.99502
multi-qa-distilbert-dot-v1        0.32681  0.34056  ...     0.95661      0.99360
multi-qa-distilbert-cos-v1        0.41881  0.42913  ...     0.98222      0.99431
msmarco-distilbert-base-tas-b     0.33946  0.35126  ...     0.94168      0.99431
msmarco-distilbert-dot-v5         0.26949  0.28396  ...     0.90612      0.98720
msmarco-bert-co-condensor         0.30729  0.32027  ...     0.89047      0.98293
msmarco-roberta-base-ance-firstp  0.33308  0.34475  ...     0.93457      0.99004

[12 rows x 12 columns]



---



**FIQA** - [Homepage](https://sites.google.com/view/fiqa/home) - [Paper](https://www.researchgate.net/publication/324629350_WWW'18_Open_Challenge_Financial_Opinion_Mining_and_Question_Answering)

In [ ]:
pd.concat([fq_als, fq_amp, fq_adr, fq_aml, fq_mmp, fq_mml, fq_mdd, fq_mdc, fq_msdd, fq_msdc, fq_msbc, fq_msra])

MAP@10  MAP@100  ...  Recall@100  Recall@1000
allenai-specter                   0.03782  0.04428  ...     0.23704      0.50673
all-mpnet-base-v2                 0.41117  0.43167  ...     0.81969      0.96187
all-distilroberta-v1              0.31174  0.33246  ...     0.73675      0.92236
all-MiniLM-L12-v2                 0.29694  0.31593  ...     0.70017      0.90838
multi-qa-mpnet-base-dot-v1        0.40186  0.42360  ...     0.80788      0.94560
multi-qa-MiniLM-L6-cos-v1         0.28995  0.30868  ...     0.68812      0.89008
multi-qa-distilbert-dot-v1        0.34930  0.36924  ...     0.75268      0.92694
multi-qa-distilbert-cos-v1        0.32248  0.34045  ...     0.72436      0.90863
msmarco-distilbert-base-tas-b     0.23319  0.24772  ...     0.59293      0.80835
msmarco-distilbert-dot-v5         0.22339  0.23781  ...     0.57077      0.79600
msmarco-bert-co-condensor         0.21913  0.23480  ...     0.60695      0.84851
msmarco-roberta-base-ance-firstp  0.22782  0.24188  ...     0.58056      0.80218

[12 rows x 12 columns]

end of fun.